In [ ]:
!pip install -q newspaper3k
!pip install scholarly
!pip install fake-useragent --upgrade
from scholarly import scholarly
import pandas as pd

In [ ]:
# Set up a ProxyGenerator object to use free proxies
# This needs to be done only once per session
from scholarly import ProxyGenerator
from getpass import getpass

pg = ProxyGenerator()
#pg.FreeProxies()

# If prompted for API KEY, use 'f1 1b b9 a208d375cc8a3 5d56 2b06087 78' (no spaces)

payload = {'api_key': getpass("Enter your ScraperAPI key:"), }
proxy_works = pg.ScraperAPI(payload['api_key'])
if proxy_works is True:
   print("Using ScraperAPI!")
else:
   print("Uh oh")

scholarly.use_proxy(pg)

Enter your ScraperAPI key:··········
Using ScraperAPI!


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install -q --upgrade GoogleNews

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 2.8 MB/s eta 0:00:00


In [ ]:
import newspaper
import json

url = 'https://www.scielo.org.mx/scielo.php?pid=S1405-04712014000500002&script=sci_arttext&tlng=en'

article = newspaper.Article(url=url, language='en')
article.download()
article.parse()

article ={
    "title": str(article.title),
    "text": str(article.text),
    "published_date": str(article.publish_date),
}

In [ ]:
titles = []
urls = []
pub_years = []
citations = []

In [ ]:
### Google scholar scraper
## How to use:
#  enter list of phrases to search in google scholar in 'queries'
#  enter desired number of results per phrase in 'num_papers'

# try not to run cell too much or overload scraper, as the proxy will break.

# Edit these
num_papers = 100
queries = ["mangrove forests"
          , "mangrove conservation"
          , "mangrove policy"
          , "mangrove restoration"
          , "mangrove deforestation"
          , "mangrove ecosystem"
          , "mangrove protection"
          , "mangrove satellite"
          , "mangrove preservation"
          , "mangrove sustainability"
          ]

for query in queries:
  q = scholarly.search_pubs(query)
  print("Querying " + query)
  for _ in range(num_papers):

      search = next(q)
      if 'pub_url' in search:
          titles.append(search['bib']['title'])
          urls.append(search['pub_url'])
          pub_years.append(search['bib']['pub_year'])
          citations.append(search['num_citations'])


Querying mangrove forests
Querying mangrove conservation
Querying mangrove policy
Querying mangrove restoration
Querying mangrove deforestation
Querying mangrove ecosystem
Querying mangrove protection
Querying mangrove satellite
Querying mangrove preservation
Querying mangrove sustainability


In [ ]:
num_papers = 200
queries = ["mangrove forests"
          , "mangrove conservation"
          , "mangrove policy"
          , "mangrove restoration"
          , "mangrove deforestation"
          , "mangrove ecosystem"
          , "mangrove protection"
          , "mangrove satellite"
          , "mangrove preservation"
          , "mangrove sustainability"
          ]

for query in queries:
  q = scholarly.search_pubs(query)
  print("Querying " + query)
  for _ in range(num_papers):

      search = next(q)
      if 'pub_url' in search:
          titles.append(search['bib']['title'])
          urls.append(search['pub_url'])
          pub_years.append(search['bib']['pub_year'])
          citations.append(search['num_citations'])

Querying mangrove forests
Querying mangrove conservation
Querying mangrove policy
Querying mangrove restoration
Querying mangrove deforestation
Querying mangrove ecosystem


MaxTriesExceededException: Cannot Fetch from Google Scholar.

In [ ]:
 column_names = ["title", 'url', "publication yr", "citations"]
df_gs = pd.DataFrame(columns = column_names)

df_gs['title'] = titles
df_gs['url'] = urls
df_gs['publication yr'] = pub_years
df_gs['citations'] = citations

df_gs = df_gs.drop_duplicates()
df_gs


title  \
0     The state of the world's mangrove forests: pas...   
1     Present state and future of the world's mangro...   
2     A review of remote sensing for mangrove forest...   
3      The impact of climate change on mangrove forests   
4     Different kinds of mangrove forests provide di...   
...                                                 ...   
2119  An analysis of fisheries exploitation and mana...   
2120                               World Mangrove Alias   
2121  Economic values of ecological services from a ...   
2122  Anthropogenic disturbance of Caribbean mangrov...   
2123       Ecosystem services of mangroves: An overview   

                                                    url publication yr  \
0     https://www.annualreviews.org/doi/abs/10.1146/...           2019   
1     https://www.cambridge.org/core/journals/enviro...           2002   
2     https://www.sciencedirect.com/science/article/...           2019   
3     https://link.springer.com/article/10.1007/s406...           2015   
4     https://onlinelibrary.wiley.com/doi/abs/10.111...           1998   
...                                                 ...            ...   
2119  https://www.sciencedirect.com/science/article/...           2007   
2120  https://www.academia.edu/download/104116790/Wo...           1997   
2121        https://pdf.usaid.gov/pdf_docs/PNACP233.pdf           1998   
2122               https://www.jstor.org/stable/2389096           1996   
2123  https://link.springer.com/chapter/10.1007/978-...           2020   

      citations  
0           535  
1          2618  
2           301  
3           490  
4           785  
...         ...  
2119        156  
2120       1354  
2121         55  
2122        397  
2123         40  

[1172 rows x 4 columns]

In [ ]:
df_gs_text = df_gs['url'].apply(extract_article_content)
df_gs['text'] = df_gs_text
df_gs = df_gs.drop(df_gs[df_gs['text'] == "None"].index)
df_gs

title  \
0     The state of the world's mangrove forests: pas...   
1     Present state and future of the world's mangro...   
3      The impact of climate change on mangrove forests   
6        Carbon cycling and storage in mangrove forests   
7                    The energetics of mangrove forests   
...                                                 ...   
2109      Water quality and mangrove ecosystem dynamics   
2114  Isolation and enzyme bioprospection of endophy...   
2115  Mangrove root: adaptations and ecological impo...   
2121  Economic values of ecological services from a ...   
2123       Ecosystem services of mangroves: An overview   

                                                    url publication yr  \
0     https://www.annualreviews.org/doi/abs/10.1146/...           2019   
1     https://www.cambridge.org/core/journals/enviro...           2002   
3     https://link.springer.com/article/10.1007/s406...           2015   
6     https://www.annualreviews.org/doi/abs/10.1146/...           2014   
7     https://books.google.com/books?hl=en&lr=&id=tH...           2009   
...                                                 ...            ...   
2109  https://books.google.com/books?hl=en&lr=&id=Yg...           1981   
2114  https://link.springer.com/article/10.1186/2193...           2014   
2115  https://link.springer.com/article/10.1007/s004...           2016   
2121        https://pdf.usaid.gov/pdf_docs/PNACP233.pdf           1998   
2123  https://link.springer.com/chapter/10.1007/978-...           2020   

      citations                                               text  
0           535  Intertidal mangrove forests are a dynamic ecos...  
1          2618  Crossref Citations\n\nThis article has been ci...  
3           490  Living at the interface between land and sea i...  
6          1411  Mangroves are ecologically and economically im...  
7           986  Try the new Google Books\n\nCheck out the new ...  
...         ...                                                ...  
2109         33  Try the new Google Books\n\nCheck out the new ...  
2114        146  Sample collection\n\nBranches from five random...  
2115        193  Agoramoorthy G, Chen FA, Hsu MJ (2008) Threat ...  
2121         55                                                     
2123         40  Banerjee, L. K., & Das, G. C. (1972). New dist...  

[588 rows x 5 columns]

In [ ]:
df_gs.to_csv()

',title,url,publication yr,citations,text\n0,"The state of the world\'s mangrove forests: past, present, and future",https://www.annualreviews.org/doi/abs/10.1146/annurev-environ-101718-033302,2019,535,"Intertidal mangrove forests are a dynamic ecosystem experiencing rapid changes in extent and habitat quality over geological history, today and into the future. Climate and sea level have drastically altered mangrove distribution since their appearance in the geological record ∼75 million years ago (Mya), through to the Holocene. In contrast, contemporary mangrove dynamics are driven primarily by anthropogenic threats, including pollution, overextraction, and conversion to aquaculture and agriculture. Deforestation rates have declined in the past decade, but the future of mangroves is uncertain; new deforestation frontiers are opening, particularly in Southeast Asia and West Africa, despite international conservation policies and ambitious global targets for rehabilitation. In addition,

In [ ]:

# Open a CSV file in write mode
with open('/content/drive/MyDrive/article_texts.csv', 'w', newline='', encoding='utf-8') as csvfile:
    # Create a CSV writer object
    writer = csv.writer(csvfile)

    # Write the header row
    writer.writerow(['text'])

    # Iterate through each URL in the list
    for url in selected_links:
        # Extract article content
        text_content = extract_article_content(url)

        # Write the text content to the CSV file
        if text_content is not None and not any(phrase in text_content.lower() for phrase in ['404', 'page not found', 'copyright', 'cookies', 'the page']):
            writer.writerow([text_content])
            print("extracted")

In [ ]:
from GoogleNews import GoogleNews
googlenews = GoogleNews()

In [ ]:
googlenews = GoogleNews(lang='en')
googlenews.get_news('mangrove conservation')
googlenews.search('mangrove conservation')

In [ ]:
result_0 = googlenews.page_at(1)

desc_1 = googlenews.get_texts()
link_1 = googlenews.get_links()

for i in list(range(2, 70)):

    result = googlenews.page_at(i)
    desc = googlenews.get_texts()
    link = googlenews.get_links()

    desc_1 = desc_1 + desc
    link_1 = link_1 + link

In [ ]:
import pandas as pd

column_names = ["description_text", 'link']
df = pd.DataFrame(columns = column_names)

df['description_text'] = desc_1
df['link'] = link_1
df

description_text  \
0      Office of Resilience and Coastal Protection (G...   
1      Healthy mangrove forests can help protect inla...   
2      FORT MYERS | SCCF starts mangrove restoration ...   
3      Sulawesi sea nomads who inspired Avatar movie ...   
4      Has nature rebounded on Sanibel Island, Captiv...   
...                                                  ...   
42875  How mangrove forests helped stall environmenta...   
42876  Studying mangrove genetic diversity in Africa ...   
42877  Govt prepares plan for mangrove conservation |...   
42878  Lamu women spearhead mangrove conservation eff...   
42879  AFRICA: EU grants €9.9m to FDA and WIA for wet...   

                                                    link  
0      news.google.com/articles/CBMiOWh0dHBzOi8vZmxvc...  
1      news.google.com/articles/CBMieGh0dHBzOi8veWFsZ...  
2      news.google.com/articles/CBMid2h0dHBzOi8vd3d3L...  
3      news.google.com/articles/CBMicGh0dHBzOi8vbmV3c...  
4      news.google.com/articles/CBMikAFodHRwczovL3d3d...  
...                                                  ...  
42875  https://www.bbc.com/future/article/20210423-ke...  
42876  https://phys.org/news/2021-04-mangrove-genetic...  
42877  https://www.thecitizen.co.tz/tanzania/news/nat...  
42878  https://www.the-star.co.ke/counties/coast/2021...  
42879  https://www.afrik21.africa/en/africa-eu-grants...  

[42880 rows x 2 columns]

In [ ]:
import numpy as np

def select_random_links(links_array, num_links):
    """
    Randomly select a given number of links from a NumPy array of links, excluding those starting with 'news.google'.

    Args:
    - links_array (numpy.ndarray): Array containing links.
    - num_links (int): Number of links to select.

    Returns:
    - selected_links (numpy.ndarray): Array containing randomly selected links.
    """
    # Convert all elements to strings
    links_array = np.array(links_array, dtype=str)

    # Randomly select links
    selected_links = np.random.choice(links_array, size=num_links, replace=False)
    return selected_links

# Example usage:
links_array = df['link']
num_links = 4000
selected_links = select_random_links(links_array, num_links)
print(len(selected_links))


4000


In [ ]:
selected_links = selected_links[1000:4000]

In [ ]:
import newspaper
import json

def extract_article_content_(url):
    """
    Extracts the content (title, text, and published date) from a given URL using the newspaper library.

    Args:
    - url (str): URL of the article.

    Returns:
    - article (dict): Dictionary containing the title, text, and published date of the article.
    """

    # Create a newspaper Article object
    article_obj = newspaper.Article(url=url, language='en')
    # Download and parse the article content
    article_obj.download()
    article_obj.parse()
    article = str(article_obj.text)
    return article

# Example usage:
url = 'https://blog.nationalgeographic.org/2024/02/07/new-study-by-national-geographic-explorers-provides-first-ever-comprehensive-assessment-of-ecosystem-services-of-brazils-coastal-mangrove-forests/'
article_info = extract_article_content(url)
article_info


'Em português\n\nReleased today, a new study provides the first-ever empirical assessment of ecosystem services — the benefits we receive from nature — of Brazilian mangroves. The study, titled “Flow of mangrove ecosystem services to coastal communities in the Brazilian Amazon” published by Frontiers in Environmental Science and co-authored by National Geographic Explorers Margaret Awuor Owuor and Angelo Bernardino, gives evidence of the critical environmental, social, economic, and cultural value mangroves hold for coastal communities.\n\nBrazil has the second largest mangrove area in the world, housing 700,000 hectares of mangroves within the Amazonian border. Awuor Owuor and Bernardino’s study, conducted in 13 communities along the northern Amazon coast of Pará, found that the healthy functioning of mangrove forests provides essential ecosystem services for local coastal communities including: food sources, cultural activities, income, education, climate regulation, and flood contro

In [ ]:
import csv

# Function to extract article content
def extract_article_content(url):
    """
    Extracts the content (text) from a given URL using the newspaper library.

    Args:
    - url (str): URL of the article.

    Returns:
    - text (str): Text content of the article.
    """
    try:
        # Create a newspaper Article object
        article_obj = newspaper.Article(url=url, language='en')

        # Download and parse the article content
        article_obj.download()
        article_obj.parse()

        # Return the text content of the article
        return str(article_obj.text)
    except Exception as e:
        #print(f"Error occurred while extracting content from {url}: {e}")
        return "None"



In [ ]:

# Open a CSV file in write mode
with open('/content/drive/MyDrive/article_texts.csv', 'w', newline='', encoding='utf-8') as csvfile:
    # Create a CSV writer object
    writer = csv.writer(csvfile)

    # Write the header row
    writer.writerow(['text'])

    # Iterate through each URL in the list
    for url in selected_links:
        # Extract article content
        text_content = extract_article_content(url)

        # Write the text content to the CSV file
        if text_content is not None and not any(phrase in text_content.lower() for phrase in ['404', 'page not found', 'copyright', 'cookies', 'the page']):
            writer.writerow([text_content])
            print("extracted")


NameError: name 'selected_links' is not defined

In [ ]:
df['text'] = df['text'].str.replace('\n', ' ')
df

text
0   If you’ve visited Singapore’s Sungei Buloh Wet...
1   Special Assistant to the Prime Minister on Ove...
2   Mangrove restoration should include social asp...
3   A model for an effective melange of mangrove c...
4   They are among the most carbon-rich forests in...
5   Congress leader Sachin Pilot on Tuesday allege...
6   The Sundarbans, the world's largest mangrove f...
7   July 26, 2023 07:53 pm | Updated 07:53 pm IST ...
8   Kendal Blust/KJZZ Mangoves grow in an estuary ...
9   Socioecological system  Mangrove forests are a...
10  KARACHI: While the overall cover of mangroves ...
11  (Seychelles News Agency) - Scientists and rese...
12  Barmer and Jaisalmer, known for their arid lan...
13  Upon arrival at Kyaukpyu Airport from Yangon, ...
14  Apple on Friday announced a new partnership wi...
15  Exactly twenty years after it was introduced, ...
16  Published : Dec 28, 2022 11:35 IST  On Decembe...
17  Mangrove planting initiative takes root in Nor...
18  By DENISE MAYCOCK  Tribune Freeport Reporter  ...
19  According to an article by Richard Harris of Q...
20  Country  Afghanistan Åland Islands Albania Alg...
21  July 04, 2023 12:09 pm | Updated 12:10 pm IST ...
22  26 Jul 2022  | 06:04am IST  SAVING THE LIFE-GI...
23  Mangrove planting activity at Kidundu, Kilifi....
24  Mangroves are one of Florida's true natives. T...
25  This article has been reviewed according to Sc...
26  Significant genetic structure was observed wit...
27  Sula E Vanderplank is an adjunct professor at ...
28  The world’s mangroves 2000–2020 report is now ...
29  Mangroves are often misunderstood and underval...
30  We extend a previously developed one-dimension...
31  Study area  Our study area encompassed the glo...
32  Financial roadmap for mangrove protection and ...
33  The Blue Carbon Explorer is a Google Earth Eng...
34  Mangroves are some of the planet’s most unique...
35  Overall simulation approach  We estimated net ...
36  [This text was generated using artificial inte...
37  Boyd, R., Dalrymple, R. & Zaitlin, B. A. Class...
38  To the Editor — Lee and colleagues1 compelling...
39  The present study makes an attempt to prioriti...
40  Mangrove cover change variables. We used the G...
41  The improved performance of the mangrove LUE m...
42  Empirical findings  We stratify cyclone exposu...
43  You can also search for this author in PubMed ...
44  We found that mangrove deforestation is often,...

In [ ]:
# Assuming df is your DataFrame
# Drop rows where 'text' column contains any of the specified phrases or is NaN
df = df[~df['text'].str.lower().str.contains('404|page not found|copyright|cookies|the page you have requested|the page', na=False)]

# Reset index after dropping rows
df.reset_index(drop=True, inplace=True)

In [ ]:
# Assuming df is your DataFrame
# Drop rows with NaN values
df.dropna(inplace=True)

# Reset index after dropping rows
df.reset_index(drop=True, inplace=True)

In [ ]:

# Assuming df is your DataFrame
# Drop duplicate rows
df.drop_duplicates(inplace=True)

# Reset index after dropping duplicates
df.reset_index(drop=True, inplace=True)


In [ ]:
df.shape

(28, 1)

In [ ]:
# Assuming df is your DataFrame and 'text' is the column containing the text data
total_word_count = df['text'].str.split().apply(len).sum()

print("Total word count:", total_word_count)


Total word count: 13762


In [ ]:
df

text
0   If you’ve visited Singapore’s Sungei Buloh Wet...
1   Special Assistant to the Prime Minister on Ove...
2   Mangrove restoration should include social asp...
3   A model for an effective melange of mangrove c...
4   They are among the most carbon-rich forests in...
5   Congress leader Sachin Pilot on Tuesday allege...
6   Blog |\n\nWetlands, often overlooked and under...
7   The Sundarbans, the world's largest mangrove f...
8   July 26, 2023 07:53 pm | Updated 07:53 pm IST ...
9   Kendal Blust/KJZZ Mangoves grow in an estuary ...
10  From 30 November to 12 December 2023, IUCN wil...
11  Socioecological system\n\nMangrove forests are...
12  KARACHI: While the overall cover of mangroves ...
13  (Seychelles News Agency) - Scientists and rese...
14  Barmer and Jaisalmer, known for their arid lan...
15  Upon arrival at Kyaukpyu Airport from Yangon, ...
16  Apple on Friday announced a new partnership wi...
17  Exactly twenty years after it was introduced, ...
18  Published : Dec 28, 2022 11:35 IST\n\nOn Decem...
19  Mangrove planting initiative takes root in Nor...
20  By DENISE MAYCOCK\n\nTribune Freeport Reporter...
21  According to an article by Richard Harris of Q...
22  Country\n\nAfghanistan Åland Islands Albania A...
23  July 04, 2023 12:09 pm | Updated 12:10 pm IST ...
24  It looks like nothing was found at this locati...
25  26 Jul 2022\n\n| 06:04am IST\n\nSAVING THE LIF...
26  Mangrove planting activity at Kidundu, Kilifi....
27  Mangroves are one of Florida's true natives. T...

In [ ]:
url_list = ['https://www.nature.com/articles/s41559-019-0942-y',
            'https://www.nature.com/articles/s41598-022-24953-5',
            'https://www.nature.com/articles/s41467-022-33962-x',
            'https://www.nature.com/articles/s41598-022-06231-6',
            'https://www.nature.com/articles/s41598-021-94207-3',
            'https://www.nature.com/articles/nindia.2017.44',
            'https://www.nature.com/articles/d44151-023-00008-0',
            'https://www.nature.com/articles/s41598-020-63880-1']

output_list = []
for url in url_list:
  output_list.append(extract_article_content(url))



In [ ]:
output_list

['To the Editor — Lee and colleagues1 compellingly suggest that restoring mangrove cover by using the widely practiced planting of mangroves, particularly monogeneric stands of Rhizophora (stilted mangroves), is not the solution to mangrove loss. They suggest that mangrove recovery must include protection of the remaining habitat and restoration of the degraded habitat, particularly in mangrove lands converted for shrimp aquaculture and agriculture. However, for mangrove recovery to be achieved, the drivers of inappropriate and ineffective mangrove planting programs must explicitly be considered.\n\nInappropriate mangrove planting programs often occur when project managers respond to inappropriate performance metrics imposed by external funding agencies, with short time frames for delivery. This process precludes both attention to the underlying drivers of mangrove deforestation, which often relate to inequality and land tenure2, and the development of participatory community restorati

In [ ]:
for element in output_list:
    df = df.append({'text': element}, ignore_index=True)

<ipython-input-89-db558a571c56>:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'text': element}, ignore_index=True)
<ipython-input-89-db558a571c56>:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'text': element}, ignore_index=True)
<ipython-input-89-db558a571c56>:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'text': element}, ignore_index=True)
<ipython-input-89-db558a571c56>:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'text': element}, ignore_index=True)
<ipython-input-89-db558a571c56>:2: FutureWarning: The frame.append method is deprecated and will be removed 

In [ ]:
# Filter out rows with text length less than 100 characters
df = df[df['text'].str.len() >= 150]

# Print the DataFrame after filtering
print(df)


                                                 text
0   If you’ve visited Singapore’s Sungei Buloh Wet...
1   Special Assistant to the Prime Minister on Ove...
2   Mangrove restoration should include social asp...
3   A model for an effective melange of mangrove c...
4   They are among the most carbon-rich forests in...
5   Congress leader Sachin Pilot on Tuesday allege...
6   The Sundarbans, the world's largest mangrove f...
7   July 26, 2023 07:53 pm | Updated 07:53 pm IST ...
8   Kendal Blust/KJZZ Mangoves grow in an estuary ...
9   Socioecological system\n\nMangrove forests are...
10  KARACHI: While the overall cover of mangroves ...
11  (Seychelles News Agency) - Scientists and rese...
12  Barmer and Jaisalmer, known for their arid lan...
13  Upon arrival at Kyaukpyu Airport from Yangon, ...
14  Apple on Friday announced a new partnership wi...
15  Exactly twenty years after it was introduced, ...
16  Published : Dec 28, 2022 11:35 IST\n\nOn Decem...
17  Mangrove planting initia

In [ ]:
df.drop_duplicates(inplace=True)

In [ ]:
# Assuming df is your DataFrame and 'text' is the column containing the text data
total_word_count = df['text'].str.split().apply(len).sum()

print("Total word count:", total_word_count)


Total word count: 41245


In [ ]:
df.to_csv('/content/drive/MyDrive/article_texts.csv', index=False)

In [ ]:
# Create a new file to store the combined text
output_file = '/content/drive/MyDrive/mangrove_text.txt'

# Open the file in write mode
with open(output_file, 'w', encoding='utf-8') as f:
    # Iterate through each row of the DataFrame
    for index, row in df.iterrows():
        # Extract the text from the 'text' column
        text = row['text']

        # Write the text to the file
        f.write(text)
        f.write('\n\n')